In [103]:
import pandas as pd
import requests
import folium
from folium.plugins import HeatMap
import geopandas

In [97]:
#crime dataset API from the fortworth city. I decieded not to use it. 
url = "https://data.fortworthtexas.gov/resource/k6ic-7kp7.json"
response = requests.get(url)
df = pd.json_normalize(response.json())
df


case_no_offense    case_no            reported_date       nature_of_call  \
0     180094593-35A  180094593  2018-10-22T18:15:00.000  NARCOTIC VIOLATIONS   
1     200085517-90Z  200085517  2020-11-03T13:24:00.000               HARASS   
2     210012743-240  210012743  2021-02-20T20:27:59.000           AUTO THEFT   
3     190047946-35A  190047946  2019-06-04T01:33:00.000  NARCOTIC VIOLATIONS   
4     190031427-90D  190031427  2019-04-13T02:44:00.000                  DWI   
..              ...        ...                      ...                  ...   
995   190086926-13B  190086926  2019-10-06T14:41:54.000              ASSAULT   
996   190088569-240  190088569  2019-10-11T13:00:00.000           AUTO THEFT   
997   190086244-240  190086244  2019-10-04T02:07:00.000           AUTO THEFT   
998   190086244-23H  190086244  2019-10-04T02:07:00.000           AUTO THEFT   
999   190089117-90Z  190089117  2019-10-13T16:23:35.000      MISSING VEHICLE   

                   from_date offense  \
0    2018-10-22T18:15:00.000     35A   
1    2020-08-12T05:18:00.000     90Z   
2    2021-02-20T20:27:59.000     240   
3    2019-06-04T01:33:49.000     35A   
4    2019-04-13T02:44:37.000     90D   
..                       ...     ...   
995  2019-10-06T14:41:54.000     13B   
996  2019-10-02T17:30:00.000     240   
997  2019-10-04T00:08:00.000     240   
998  2019-10-04T00:08:00.000     23H   
999  2019-10-10T00:01:00.000     90Z   

                                          offense_desc  \
0    HSC 481.115(B) Poss CS PG 1 <1G 35A DRUG/NARCOTIC   
1                               PC 42.07(C) Harassment   
2    PC 31.03(E)(4)(A)AUTO Theft>$1500<$20K (Auto t...   
3    HSC 481.117(B) Poss CS PG 3 <28G 35A DRUG/NARC...   
4    PC 49.04 Driving While Intoxicated 90D DRIVING...   
..                                                 ...   
995  PC 22.01(A)(1)FV Aslt Causes B/I Family Member...   
996  PC 31.03 - AUTO Auto Theft 240 MOTOR VEHICLE T...   
997  PC 31.03(E)(4)(A)AUTO2015 Theft Prop>=$2500<$3...   
998  PC 31.03(E)(2)(A)(1) Theft>=$50<$500 23H ALL O...   
999  PC 21.19 Unlawful Electronic Transmission of S...   

                      block_address        city state  ...   division  \
0          700 CALIFORNIA PKWY N WB  FORT WORTH    TX  ...        NaN   
1               1300 MARLBOROUGH DR  FORT WORTH    TX  ...      South   
2           SANDY LN & EDERVILLE RD  FORT WORTH    TX  ...       East   
3     OAK GROVE RD / E IH 20 FWY EB         NaN    TX  ...        NaN   
4    WEST FWY SR WB / GREEN OAKS RD         NaN    TX  ...        NaN   
..                              ...         ...   ...  ...        ...   
995                  8100 PASEO TRL  FORT WORTH    TX  ...        NaN   
996         WEST LOOP 820 SOUTH FWY  FORT WORTH    TX  ...       West   
997                500 MEACHAM BLVD  FORT WORTH    TX  ...  Northwest   
998                500 MEACHAM BLVD  FORT WORTH    TX  ...  Northwest   
999             8800 OCEAN VIEW AVE    whittier    CA  ...        NaN   

    councildistrict :@computed_region_nnh8_mcwc :@computed_region_yjg4_vj9w  \
0               NaN                         NaN                         NaN   
1                 8                           8                        2666   
2                 5                         NaN                         NaN   
3               NaN                         NaN                         NaN   
4               NaN                         NaN                         NaN   
..              ...                         ...                         ...   
995             NaN                           3                        1333   
996               3                         NaN                         NaN   
997               2                         NaN                         NaN   
998               2                         NaN                         NaN   
999             NaN                         NaN                         NaN   

    :@computed_region_bgtw_5uv7 :@compu

In [98]:
df = pd.read_csv("datasets/fort-worth-texas-crime-data.csv")
df["Longitude"].values

array([-97.37088667, -97.38530297, -97.29053048, ..., -97.28785832,
       -97.30470055, -97.33772489])

# Heat Map of crime in the Forth Worth Area

In [99]:
map = folium.Map(location=(32.7555, -97.3308), zoom_start=12)

sample_size = 1000
    
location_data = pd.DataFrame({"latitude":df["Latitude"].values,"longitude": df["Longitude"].values})
location_data["cordinates"] = list(zip(location_data['latitude'], location_data['longitude']))

random_vals = location_data["cordinates"].sample(n=sample_size).values

    
HeatMap(random_vals).add_to(map)
map

# Locations of Mediterranean Restraunts

In [100]:
df = pd.read_csv("datasets/restaurants.csv")

for row in df.itertuples():
    
    folium.Marker(
        location=(row.Latitude,row.Longitude), 
        tooltip=row.Name,
        popup=f"Rating: {row.Rating}",
        icon=folium.Icon(color="green"),
    ).add_to(map)
    
map

In [136]:
map = folium.Map(location=(32.7555, -97.3308), zoom_start=12)

geo_data = geopandas.read_file(
    "datasets/kx-fort-worth-texas-zip-codes-SHP.zip"
)

zipcode_data = pd.read_csv(
    "datasets/census_data_output.csv"
)

delta = (zipcode_data["Median Household Income"].max() - zipcode_data["Median Household Income"].min())/10
bins = [(zipcode_data["Median Household Income"].min() + i * delta) for i in range(9)]

folium.Choropleth(
    geo_data=geo_data,
    data=zipcode_data,
    fill_color="YlGn",
    columns=["ZIP_Code", "Median Household Income"],
    key_on="feature.properties.POSTAL",
    bins=8,
).add_to(map)
map